In [1]:
from google.colab import drive
drive.mount('/content/drive')
NUM_TRIALS = 20

Mounted at /content/drive


In [2]:
pip install gspread==3.6


  Found existing installation: gspread 3.0.1
    Uninstalling gspread-3.0.1:
      Successfully uninstalled gspread-3.0.1


In [3]:

import numpy as np
import pdb
import pandas as pd
import numbers
from google.colab import auth
import os
# auth.authenticate_user()

import gspread 
from oauth2client.client import GoogleCredentials

my_json = '{"access_token": null, "client_id": "32555940559.apps.googleusercontent.com", "client_secret": "ZmssLNjJy2998hD4CTg2ejr2", "refresh_token": "1//05jJdSPJetzqsCgYIARAAGAUSNwF-L9IrC9Z2KZtw_HEeZhH2aTBd8tpq3xmUCSbK_4ZBvRXMzpeQh7R28VjLV3laqoigF0qA4Rc", "token_expiry": null, "token_uri": "https://oauth2.googleapis.com/token", "user_agent": "Python client library", "revoke_uri": "https://oauth2.googleapis.com/revoke", "id_token": null, "id_token_jwt": null, "token_response": null, "scopes": [], "token_info_uri": null, "invalid": false, "_class": "GoogleCredentials", "_module": "oauth2client.client"}'

gc = gspread.authorize(GoogleCredentials.from_json(my_json))
# gc = gspread.authorize(GoogleCredentials.get_application_default())
wb = gc.open_by_url('https://docs.google.com/spreadsheets/d/1F8A5n3WVr9WXHDXZhv2w0BPaMC8uymUyxEWdI9UX6xg/edit#gid=0')

In [4]:
%%writefile setup.sh

git clone https://github.com/NVIDIA/apex
pip install -v --no-cache-dir --global-option="--cpp_ext" --global-option="--cuda_ext" ./apex

Writing setup.sh


In [5]:
# !sh setup.sh

In [6]:
# %cd drive/My Drive/mixout/

In [7]:
!git clone https://github.com/leedtan/ModernML_TinyBert.git

Cloning into 'ModernML_TinyBert'...
remote: Enumerating objects: 12, done.
remote: Counting objects: 100% (12/12), done.
remote: Compressing objects: 100% (9/9), done.
remote: Total 903 (delta 5), reused 9 (delta 3), pack-reused 891
Receiving objects: 100% (903/903), 23.29 MiB | 13.02 MiB/s, done.
Resolving deltas: 100% (592/592), done.


In [8]:
os.chdir('ModernML_TinyBert')
# !python download_glue_data.py

In [9]:
os.chdir('revisit-bert-finetuning')

In [10]:
!pip install transformers==2.8.0

     |████████████████████████████████| 573kB 12.6MB/s 
     |████████████████████████████████| 890kB 30.4MB/s 
     |████████████████████████████████| 5.6MB 48.7MB/s 
     |████████████████████████████████| 133kB 57.8MB/s 
     |████████████████████████████████| 1.2MB 51.7MB/s 
     |████████████████████████████████| 7.3MB 54.4MB/s 
     |████████████████████████████████| 81kB 10.0MB/s 
  Created wheel for sacremoses: filename=sacremoses-0.0.43-cp37-none-any.whl size=893262 sha256=e192442d44d3a8e3d7446a1a7d5e2f9b5eec74088c063327c402de734515a14f
  Stored in directory: /root/.cache/pip/wheels/29/3c/fd/7ce5c3f0666dab31a50123635e6fb5e19ceb42ce38d4e58f45
Successfully built sacremoses
ERROR: botocore 1.20.33 has requirement urllib3<1.27,>=1.25.4, but you'll have urllib3 1.24.3 which is incompatible.


In [11]:
# works:
# !git checkout 7589fbb94924c50ae9a47094729c16803a280d64
# !git checkout 6a8da1135ae21c6bdd3d1d983b8aea90736736eb
# !git checkout d3c118f11cf4035feca957eff7b34b4413f3c5d6
!git checkout hans

Branch 'hans' set up to track remote branch 'hans' from 'origin'.
Switched to a new branch 'hans'


In [12]:
!cat ryan.sh

cat: ryan.sh: No such file or directory


In [13]:
!git pull

Already up to date.


In [14]:
!python train_to_sheet.py

python3: can't open file 'train_to_sheet.py': [Errno 2] No such file or directory


In [15]:

sheet = wb.worksheet('results')
def get_df(sheet):
  df = pd.DataFrame(sheet.get_all_values())
  df.columns = df.iloc[0,:]
  df.index = df.iloc[:,0]
  df = df.iloc[1:,1:]
  return df
  
def get_row_num(df, sheet, paramnames):
  if paramnames in df.index:
    rowidx = df.index.to_list().index(paramnames) + 1
  else:
    current_max_row = len(sheet.get_all_values())
    rowidx = int(current_max_row) + 1
  return rowidx
def check_run(paramnames, task, df = None, sheet = None):
  if 1:# df is None:
    df = get_df(sheet)
  if paramnames in df.index:
    idx = df.columns.to_list().index(task)
    row = df.loc[paramnames,:]
    rowiloc = row.iloc[idx+1]
    if rowiloc == '':
      return True
    if not isinstance(rowiloc, numbers.Number):
      if isinstance(rowiloc, str) and rowiloc.isnumeric():
        rowiloc = int(rowiloc)
      else:
        return False
    if rowiloc >= NUM_TRIALS:
      return False
  return True
def run(paramnames, task, df, sheet, params = {}):
  df = get_df(sheet)
  if paramnames not in df.index:
    row_idx = get_row_num(df, sheet, paramnames)
    sheet.update(f"A{row_idx}", [[paramnames]])
    df = get_df(sheet)
  row_idx = get_row_num(df, sheet, paramnames)
  df = get_df(sheet)
  idx = df.columns.to_list().index(task)
  count = df.iloc[row_idx-1, idx+1]
  if count == '':
    count = 0
    avg = 0
  avg = df.iloc[row_idx-1, idx]
  if avg == '':
    avg = 0
  avg = float(avg)
  count = int(count)
  
  all_datasets = ['rte','sts-b','mrpc','cola', 'hans', 'mnlihans']
  metrics = ['test_acc', 'test_pearson', 'test_acc', 'test_mcc', 'acc', 'acc']
  metrics = dict(zip(all_datasets, metrics))
  result_key = metrics[args.task_name.lower()]

  args.seed = seed = count + 1
  args.output_dir = (
      output_dir + "_DATASET_" + args.task_name.lower() + "_SEED_" + str(seed)
  )
  try:
    wb.add_worksheet(paramnames, 100, 10)
  except:
    pass
  sheet2 = wb.worksheet(paramnames)
  # df2 = get_df(sheet2)
  df2 = pd.DataFrame(sheet2.get_all_values())
  taskcolidx = all_datasets.index(args.task_name.lower())
  row_idx2 = df2.shape[0]


  results = run_glue_main(args)
  print('RESULTS::::')
  print(type(results))
  print(results)
  if args.task_name.lower() == 'mrpc':
    score = results['f1']
  elif 'acc' in results:
    score = results['acc']
  elif 'pearson' in results:
    score = results['pearson']
  print('avg',type(avg),avg,'count',type(count),count,'score',type(score),score,)
  newavg = (avg * count + score) / (count + 1)

  sheet2.update(f"{chr(ord('a') + taskcolidx + 1)}{row_idx2+1}", [[score]])


  sheet.update(f"{chr(ord('a') + idx + 2)}{row_idx+1}", [[count+1]])
  sheet.update(f"{chr(ord('a') + idx + 1)}{row_idx+1}", [[newavg]])

  return True
def simulate(paramnames, tasks, df = None, sheet = None, params = {}):
  if df is None:
    df = get_df(sheet)
  for task in tasks:
    i = 0
    while check_run(paramnames, task, df, sheet) and i < NUM_TRIALS:
      i += 1
      run(paramnames, task, df, sheet, params = params)
      df = get_df(sheet)

In [16]:
def dict2obj(d):
    if isinstance(d, list):
        d = [dict2obj(x) for x in d]
    if not isinstance(d, dict):
        return d
    class C(object):
        def __init__(self):
          pass
        def __call__(self):
          pass
        pass
    o = C()
    for k in d:
        o.__dict__[k] = dict2obj(d[k])
    return o
dict2obj({'b':2}).b

2

In [17]:
# args ={'model_type': 'bert', 'model_name_or_path': 'bert-large-uncased', 'task_name': 'RTE', 
#     'do_train':True, 'data_dir': "/content/drive/My Drive/mixout/ModernML_TinyBert/glue_data", 'max_seq_length': 64, 
#     'per_gpu_eval_batch_size': 8, 'weight_decay': 0, 'seed': 1, 
#     'overwrite_output_dir':True, 'do_lower_case':True, 'per_gpu_train_batch_size': 8, 
#     'gradient_accumulation_steps': 4, 'logging_steps': 0, 'num_loggings': 10, 
#     'save_steps': 0, 'test_val_split':True, 'use_torch_adamw':True, 
#     'cache_dir': "/content/drive/My Drive/mixout/ModernML_TinyBert/hf-transformers-cache" ,
#     'num_train_epochs': 3.0, 'warmup_ratio': 0.1, 'learning_rate': 2e-05 ,
#     'output_dir': 'tests/FULLTESTS/classic', 'all_datasets':True, 
#     'reinit_pooler': True, 'normalize': True, 'mixout_layers': 6, 'reinit_layers':6, 'mixout': .3, 
#     'trials': 10, 'l2_scaling':0}

# args['mixout_layers'] = 9
# args['reinit_layers'] = 3
# # args['frozen_layers'] = 4
# args['finetune_layers'] = 0
# # args['l2_reg_decay'] = 1e-1
# args['l2_reg_mult'] = 1e-2
# args['reinit_pooler'] = True
# if 0:
#   args['reinit_pooler'] = False
#   args['newmixout'] = 1
# if 0:
#   args['newmixout'] = 0
#   args['gradient_accumulation_steps'] = 1
#   args['per_gpu_train_batch_size'] = 32
#   args['per_gpu_eval_batch_size'] = 32
#   args['reinit_pooler'] = True
#   # args['no_cuda'] = 0

In [18]:
args = {"model_type" : "bert","model_name_or_path" : "bert-base-uncased", "task_name" : "hans",
    "do_train" : True, "data_dir" : "/content/drive/My Drive/mixout/ModernML_TinyBert/glue_data","max_seq_length" : 128,
    "per_gpu_eval_batch_size" : 32,"weight_decay" : 0,"seed" : 0,
    "overwrite_output_dir" : True, "do_lower_case" : True, "per_gpu_train_batch_size" : 32,
    "gradient_accumulation_steps" : 1,"logging_steps" : 0,"num_loggings" : 10,
    "save_steps" : 0,"test_val_split" : True, "use_torch_adamw" : True, "cache_dir" : "/content/drive/My Drive/mixout/ModernML_TinyBert/hf-transformers-cache", 
    "num_train_epochs" : 3.0,"warmup_ratio" : 0.1,"learning_rate" : 2e-05 ,
    "output_dir" : "tests/FULLTESTS/classic","mixout" : 0.1,"no_cuda": False , "all_datasets" : True
}

for name, default_val in zip(["data_dir", "model_type", "model_name_or_path", "task_name", "output_dir",
 "config_name", "tokenizer_name", "cache_dir", "max_seq_length", "do_train","do_lower_case", "save_best",
  "save_last", "train_batch_size", "per_gpu_train_batch_size", "per_gpu_eval_batch_size", "gradient_accumulation_steps",
   "learning_rate", "layerwise_learning_rate_decay", "weight_decay", "adam_epsilon", "max_grad_norm", "num_train_epochs", 
   "max_steps", "warmup_steps", "warmup_ratio", "weight_logging_steps", "logging_steps", "num_loggings", "save_steps", 
   "no_cuda","overwrite_output_dir", "overwrite_cache", "seed", "fp16", "fp16_opt_level", "local_rank", "server_ip",
   "server_port","use_bertadam","use_torch_adamw","downsample_trainset", "resplit_val", "reinit_layers", "mixout_layers",
    "unfreeze_after_epoch", "reinit_pooler","l2_scaling","normalize","all_datasets","layer_mixout","rezero_layers", "mixout",
     "mixout_decay", "trials", "prior_weight_decay", "test_val_split",'frozen_layers', 'finetune_layers',
      'l2_reg_decay', 'l2_reg_mult', 'newmixout'], 
      [None, None, None, None, None, '', '', '', 128, False, False, False, False, 0, 8, 8,
1, 5e-5, 1.0, 0.0, 1e-8, 1.0, 3.0, -1, 0, 0, 10, 0, 0, 500, False, False, False, 42,
False, '01', -1, '', '', False, False, -1, 0, 0, 0, 0, False, False, False, False, False, 
0, 0.0, 1.0, NUM_TRIALS, False, False, 0, 0, 1.0, 3e-3, 1]):
    if name not in args:
        args[name] = default_val

In [19]:

args['task_name']

'hans'

In [20]:
# !cat /content/ModernML_TinyBert/revisit-bert-finetuning/run_glue.py

In [21]:

pdb

<module 'pdb' from '/usr/lib/python3.7/pdb.py'>

In [ ]:
from run_glue import main as run_glue_main
from options import get_parser
import os

args =dict2obj(args)
output_dir = args.output_dir
data_dir = args.data_dir

# def experiment(seeds):
#     for seed in seeds:

#         all_datasets = ['rte','sts-b','mrpc','cola', 'hans']
#         metrics = ['test_acc', 'test_pearson', 'test_acc', 'test_mcc', 'acc']
#         metrics = dict(zip(all_datasets, metrics))
#         result_key = metrics[args.task_name.lower()]

#         args.seed = seed
#         args.output_dir = (
#             output_dir + "_DATASET_" + args.task_name.lower() + "_SEED_" + str(seed)
#         )
#         results = run_glue_main(args)
#         import pdb
#         pdb.set_trace()
#         score = results[result_key]

DATASETS = ["RTE", "MRPC", "STS-B"]
# DATASETS = ["RTE"]
DATASETS = ['mnlihans']


# for dataset in DATASETS:
#     seeds = range(args.trials)
#     args.task_name = dataset
#     args.data_dir = os.path.join(data_dir, args.task_name)
#     experiment(seeds)
def run_real(paramnames, tasks, df = None, sheet = None, params = {}):
  if df is None:
    df = get_df(sheet)
  for task in tasks:
    args.task_name = task
    # params.data_dir = os.path.join(data_dir, args.task_name)
    args.data_dir = os.path.join(data_dir, args.task_name)
    i = 0
    while check_run(paramnames, task, df, sheet) and i < NUM_TRIALS:
      i += 1
      run(paramnames, task, df, sheet, params = params)
      df = get_df(sheet)
lnum = [args.frozen_layers, args.mixout_layers, args.finetune_layers, args.reinit_layers]
paramnames = f"l_{lnum[0]}_{lnum[1]}_{lnum[2]}_{lnum[3]}_reg_{args.l2_reg_mult}_regdecay_{args.l2_reg_decay}_ep_{args.num_train_epochs}_decay_{args.l2_reg_decay}"
mix = {0:'cho',1:'ours'}[args.newmixout]
paramnames = f"mnlihans"
# paramnames = f"old_nogradacc_{lnum[0]}_{lnum[1]}_{lnum[2]}_{lnum[3]}"
# pdb.run('''run_real(paramnames, DATASETS, df = None, sheet = sheet, params = args)''')
run_real(paramnames, DATASETS, df = None, sheet = sheet, params = args)

03/21/2021 22:02:30 - WARNING - run_glue -   Process rank: -1, device: cuda, n_gpu: 1, distributed training: False, 16-bits training: False
03/21/2021 22:02:31 - INFO - filelock -   Lock 140276153991056 acquired on /root/.cache/torch/transformers/4dad0251492946e18ac39290fcfe91b89d370fee250efe9521476438fe8ca185.7156163d5fdc189c3016baca0775ffce230789d7fa2a42ef516483e4ca884517.lock
03/21/2021 22:02:31 - INFO - transformers.file_utils -   https://s3.amazonaws.com/models.huggingface.co/bert/bert-base-uncased-config.json not found in cache or force_download set to True, downloading to /root/.cache/torch/transformers/tmpu1ewxaie


03/21/2021 22:02:31 - INFO - transformers.file_utils -   storing https://s3.amazonaws.com/models.huggingface.co/bert/bert-base-uncased-config.json in cache at /root/.cache/torch/transformers/4dad0251492946e18ac39290fcfe91b89d370fee250efe9521476438fe8ca185.7156163d5fdc189c3016baca0775ffce230789d7fa2a42ef516483e4ca884517
03/21/2021 22:02:31 - INFO - transformers.file_utils -   creating metadata file for /root/.cache/torch/transformers/4dad0251492946e18ac39290fcfe91b89d370fee250efe9521476438fe8ca185.7156163d5fdc189c3016baca0775ffce230789d7fa2a42ef516483e4ca884517
03/21/2021 22:02:31 - INFO - filelock -   Lock 140276153991056 released on /root/.cache/torch/transformers/4dad0251492946e18ac39290fcfe91b89d370fee250efe9521476438fe8ca185.7156163d5fdc189c3016baca0775ffce230789d7fa2a42ef516483e4ca884517.lock
03/21/2021 22:02:31 - INFO - transformers.configuration_utils -   loading configuration file https://s3.amazonaws.com/models.huggingface.co/bert/bert-base-uncased-config.json from cache at /r

03/21/2021 22:02:34 - INFO - transformers.configuration_utils -   loading configuration file https://s3.amazonaws.com/models.huggingface.co/bert/bert-base-uncased-config.json from cache at /content/drive/My Drive/mixout/ModernML_TinyBert/hf-transformers-cache/4dad0251492946e18ac39290fcfe91b89d370fee250efe9521476438fe8ca185.7156163d5fdc189c3016baca0775ffce230789d7fa2a42ef516483e4ca884517
03/21/2021 22:02:34 - INFO - transformers.configuration_utils -   Model config BertConfig {
  "_num_labels": 2,
  "architectures": [
    "BertForMaskedLM"
  ],
  "attention_probs_dropout_prob": 0.1,
  "bad_words_ids": null,
  "bos_token_id": null,
  "decoder_start_token_id": null,
  "do_sample": false,
  "early_stopping": false,
  "eos_token_id": null,
  "finetuning_task": "mnlihans",
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "id2label": {
    "0": "LABEL_0",
    "1": "LABEL_1"
  },
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "is_decoder": false,
  "is

train1 size torch.Size([392702, 128])
eval1 size torch.Size([30000, 128])


03/21/2021 22:03:52 - INFO - run_glue -   ***** Running training *****
03/21/2021 22:03:52 - INFO - run_glue -     Num examples = 392702
03/21/2021 22:03:52 - INFO - run_glue -     Num Epochs = 3
03/21/2021 22:03:52 - INFO - run_glue -     Instantaneous batch size per GPU = 32
03/21/2021 22:03:52 - INFO - run_glue -     Total train batch size (w. parallel, distributed & accumulation) = 32
03/21/2021 22:03:52 - INFO - run_glue -     Gradient Accumulation steps = 1
03/21/2021 22:03:52 - INFO - run_glue -     Total optimization steps = 36816
iteration:   0%|          | 0/12272 [00:00<?, ?it/s]

...


iteration:  87%|████████▋ | 10700/12272 [2:32:24<13:24,  1.95it/s]03/22/2021 18:02:01 - INFO - run_glue -   Loading features from cached file /content/drive/My Drive/mixout/ModernML_TinyBert/glue_data/mnlihans/cached_dev_bert-base-uncased_128_mnlihans

iteration:  87%|████████▋ | 10701/12272 [2:32:59<4:44:52, 10.88s/it]



acc so far 10700 0.5302
trn acc 0.84375 trn loss 0.3295225203037262





iteration:  88%|████████▊ | 10800/12272 [2:33:49<12:23,  1.98it/s]03/22/2021 18:03:26 - INFO - run_glue -   Loading features from cached file /content/drive/My Drive/mixout/ModernML_TinyBert/glue_data/mnlihans/cached_dev_bert-base-uncased_128_mnlihans

iteration:  88%|████████▊ | 10801/12272 [2:34:24<4:25:39, 10.84s/it]



acc so far 10800 0.5234666666666666
trn acc 0.875 trn loss 0.2601407468318939





iteration:  89%|████████▊ | 10865/12272 [2:34:56<11:52,  1.98it/s]

In [ ]:

args.keys()

In [ ]:

type(trn_acc.cpu().detach().numpy())

In [ ]:
(outputs[1].argmax(1) == inputs['labels']).double().mean()

In [ ]:
np.mean(outputs[1].argmax(1) == inputs['labels'])

In [ ]:
!ls '/content/drive/My Drive/mixout/ModernML_TinyBert/glue_data'

In [ ]:
eval_datasets[0].tensors[0] == train_dataloader.dataset.tensors[0]

In [ ]:
# memory footprint support libraries/code
!ln -sf /opt/bin/nvidia-smi /usr/bin/nvidia-smi
!pip install gputil
!pip install psutil
!pip install humanize
import psutil
import humanize
import os
import GPUtil as GPU
GPUs = GPU.getGPUs()
# XXX: only one GPU on Colab and isn’t guaranteed
gpu = GPUs[0]
def printm():
 process = psutil.Process(os.getpid())
 print("Gen RAM Free: " + humanize.naturalsize( psutil.virtual_memory().available ), " | Proc size: " + humanize.naturalsize( process.memory_info().rss))
 print("GPU RAM Free: {0:.0f}MB | Used: {1:.0f}MB | Util {2:3.0f}% | Total {3:.0f}MB".format(gpu.memoryFree, gpu.memoryUsed, gpu.memoryUtil*100, gpu.memoryTotal))
printm()

In [ ]:
import torch
torch.cuda.empty_cache()

In [ ]:

args.data_dir

In [ ]:
# from run_glue import main as run_glue_main
# from options import get_parser
# import os

# args =dict2obj(args)
# output_dir = args.output_dir
# data_dir = args.data_dir


# DATASETS = ["RTE", "MRPC", "CoLA", "STS-B"]
# DATASETS = ["RTE", "MRPC", "STS-B"]


# def experiment(seeds):
#     for seed in seeds:
#         args.seed = seed
#         args.output_dir = (
#             output_dir + "_DATASET_" + args.task_name.lower() + "_SEED_" + str(seed)
#         )
#         run_glue_main(args)


# if __name__ == "__main__":
#     # revisiting finetuned bert (https://arxiv.org/pdf/2006.05987.pdf) uses 20 random seeds
#     seeds = range(args.trials)
#     if not args.all_datasets:
#         args.data_dir = os.path.join(data_dir, args.task_name)
#         experiment(seeds)
#     else:
#         for dataset in DATASETS:
#             args.task_name = dataset
#             args.data_dir = os.path.join(data_dir, args.task_name)
#             experiment(seeds)

In [ ]:
# !echo '''python run_glue_datasets.py \
#     --model_type bert --model_name_or_path bert-large-uncased --task_name RTE \
#     --do_train --data_dir /content/ModernML_TinyBert/glue_data/RTE --max_seq_length 16 \
#     --per_gpu_eval_batch_size 64 --weight_decay 0 --seed 0 \
#     --overwrite_output_dir --do_lower_case --per_gpu_train_batch_size 32 \
#     --gradient_accumulation_steps 1 --logging_steps 0 --num_loggings 10 \
#     --save_steps 0 --test_val_split --use_torch_adamw --cache_dir /content/ModernML_TinyBert/hf-transformers-cache \
#     --num_train_epochs 3.0 --warmup_ratio 0.1 --learning_rate 2e-05 \
#     --output_dir bert_output/REINIT5/RTE/SEED0 \
#     --reinit_pooler --reinit_layers 5''' > sample_commands/run.sh

!echo '''python run_glue_datasets.py \
    --model_type bert --model_name_or_path bert-large-uncased --task_name RTE \
    --do_train --data_dir "/content/drive/My Drive/mixout/ModernML_TinyBert/glue_data" --max_seq_length 64 \
    --per_gpu_eval_batch_size 8 --weight_decay 0 --seed 1 \
    --overwrite_output_dir --do_lower_case --per_gpu_train_batch_size 8 \
    --gradient_accumulation_steps 4 --logging_steps 0 --num_loggings 10 \
    --save_steps 0 --test_val_split --use_torch_adamw --cache_dir "/content/drive/My Drive/mixout/ModernML_TinyBert/hf-transformers-cache" \
    --num_train_epochs 3.0 --warmup_ratio 0.1 --learning_rate 2e-05 \
    --output_dir tests/FULLTESTS/classic --all_datasets \
    --reinit_pooler --normalize --mixout_layers 12 --mixout .3 \
    --trials 10''' > sample_commands/run.sh

In [ ]:
!git pull

In [ ]:
!sh sample_commands/run.sh